# IANNWTF - Homework 10
(by Group 17 - Nils Niehaus, Marlon Dammann, Philipp Bauer)
## Imports

In [13]:
import os
import re
import numpy as np

import tensorflow as tf
import tensorflow_datasets as tfds
from tensorflow.keras import layers
from tensorflow_text import RegexSplitter

from collections import Counter
from tqdm import tqdm

## Dataset

In [2]:
try:
    import google.colab
    from google.colab import drive
    os.chdir('drive/MyDrive')
    with open('./bible.txt','r') as file:
        raw_text = file.read()
except:
    with open('./bible.txt','r') as file:
        raw_text = file.read()
raw_text[0:100]

'The First Book of Moses:  Called Genesis\n\n\n1:1 In the beginning God created the heaven and the earth'

In the following we will use only regex modifications and string class methods since the bible is, compared to other data, relatively easy to preprocess.

## Word Embeddings
### Preprocessing

In [3]:
preprocessed_text = raw_text.lower()
preprocessed_text = re.sub(r'(\n)|([0123456789:;,\.?!\)\(\"\']+)',"",preprocessed_text) # Replaces all unusual characters with a space

In [4]:
text_splitter = RegexSplitter(r' ')
word_split = text_splitter.split(preprocessed_text)
word_split[0][:10]

<tf.Tensor: shape=(10,), dtype=string, numpy=
array([b'the', b'first', b'book', b'of', b'moses', b'called', b'genesis',
       b'in', b'the', b'beginning'], dtype=object)>

In [5]:
def get_n_frequent(n,word_split):
    c = Counter(word_split)
    return [word for word,count in c.most_common(n)]

In [6]:
subset = 10000
tokens = get_n_frequent(subset,word_split[0].numpy())
print('Selected the',len(tokens),'most common words.')
print(tokens[:10])

Selected the 10000 most common words.
[b'the', b'and', b'of', b'to', b'in', b'that', b'he', b'shall', b'i', b'for']


In [7]:
def get_word_context_pairs(tokens,word_split,window=4):
    context_pairs = {token : [] for token in tokens}
    for token in tqdm(tokens,desc='Retrieving context words for tokens:'):
        context_words = []
        for i in range(len(word_split)):
            if word_split[i] == token:
                for s in range(window):
                    try:
                        if word_split[i+s] in tokens:
                            context_words += [word_split[i+s]]
                    except IndexError:
                        pass
                    except Exception as e:
                        print(e)
        context_pairs[token] = list(set(context_words))
    return context_pairs

In [8]:
context_pairs = get_word_context_pairs(tokens,word_split[0].numpy())

Retrieving context words for tokens:: 100%|██████████████████████████████████████| 10000/10000 [09:46<00:00, 17.06it/s]


In [16]:
target_pairs = [[(token,target) for target in context_pairs[token]] for token in list(context_pairs.keys())]
target_pairs

[[(b'the', b'andbefore'),
  (b'the', b'curses'),
  (b'the', b'kiss'),
  (b'the', b'midianites'),
  (b'the', b'uponall'),
  (b'the', b'navy'),
  (b'the', b'himand'),
  (b'the', b'lordthy'),
  (b'the', b'bowels'),
  (b'the', b'juda'),
  (b'the', b'thecanaanite'),
  (b'the', b'midian'),
  (b'the', b'mysanctuary'),
  (b'the', b'thereapers'),
  (b'the', b'ready'),
  (b'the', b'reproach'),
  (b'the', b'sacks'),
  (b'the', b'kept'),
  (b'the', b'south'),
  (b'the', b'expert'),
  (b'the', b'flattereth'),
  (b'the', b'feast'),
  (b'the', b'andcame'),
  (b'the', b'throughout'),
  (b'the', b'gardenof'),
  (b'the', b'shittim'),
  (b'the', b'ruin'),
  (b'the', b'purple'),
  (b'the', b'pieces'),
  (b'the', b'ofan'),
  (b'the', b'endthat'),
  (b'the', b'lordgod'),
  (b'the', b'vineyard'),
  (b'the', b'zilpah'),
  (b'the', b'silver'),
  (b'the', b'receiving'),
  (b'the', b'ofesau'),
  (b'the', b'tarried'),
  (b'the', b'leahand'),
  (b'the', b'over'),
  (b'the', b'bedestroyed'),
  (b'the', b'heart'),
 

In [9]:
# data_raw = tf.data.Dataset.from_tensor_slices(word_data)

In [10]:
# def preprocess_dataset(data,context_words):
#     '''We cast the datatype into float32 and normalize'''
#     data = data.map(lambda word: (word : context_words[word]))
#     '''We shuffle, take a batch size of 64 and prefetch 20 elements.'''
#     data = data.shuffle(1000)
#     data = data.batch(64)
#     data = data.prefetch(20)
#     return data

In [11]:
# [elem for elem in data_raw.take(1)]

### Model

### Training